##**Import** arguments

In [1]:
!pip install pyLDAvis==3.2.1
!pip install spacy
!python -m spacy download pt_core_news_sm

     |████████████████████████████████| 1.7 MB 8.9 MB/s 
  Created wheel for pyLDAvis: filename=pyLDAvis-3.2.1-py2.py3-none-any.whl size=136187 sha256=4a2fcd59dd5c1adf1c71d8ad64026c2314955fc29c1054c0c5ae0399337bc278
  Stored in directory: /root/.cache/pip/wheels/c6/ee/a6/7c17a63623f940dff0b9cbd7e48a27543f088fa55a7d2b62d0
Successfully built pyLDAvis
     |████████████████████████████████| 21.2 MB 46.6 MB/s 
  Created wheel for pt-core-news-sm: filename=pt_core_news_sm-2.2.5-py3-none-any.whl size=21186282 sha256=93a6085159b57346dba82a8a04b8b3dcbb8491db951fe1a0c4ec2cda1b2eae0d
  Stored in directory: /tmp/pip-ephem-wheel-cache-3el1evvy/wheels/c3/f9/0c/5c014a36941a00f5df5fc0756cb961d7c457a978e697a6ce3b
Successfully built pt-core-news-sm
✔ Download and installation successful
You can now load the model via spacy.load('pt_core_news_sm')


In [2]:
import sqlite3
import pandas as pd
import numpy as np
import json

import nltk
import gensim
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('rslp')

import pyLDAvis.gensim
import pickle 
import pyLDAvis# Visualize the topics

import math
from matplotlib import pyplot as plt

import spacy
import io

# nlp = spacy.load('pt_core_news_sm')
import pt_core_news_sm
nlp = pt_core_news_sm.load()

from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from string import punctuation

from pprint import pprint

import logging
import itertools
logging.basicConfig(format='%(levelname)s : %(message)s', level=logging.INFO)
logging.root.level = logging.INFO  # ipython sometimes messes up the logging setup; restore

nlp = pt_core_news_sm.load()

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package rslp to /root/nltk_data...
[nltk_data]   Unzipping stemmers/rslp.zip.


/usr/local/lib/python3.7/dist-packages/past/types/oldstr.py:5: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated since Python 3.3,and in 3.9 it will stop working
  from collections import Iterable
/usr/local/lib/python3.7/dist-packages/jsonschema/compat.py:6: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated since Python 3.3,and in 3.9 it will stop working
  from collections import MutableMapping, Sequence  # noqa
/usr/local/lib/python3.7/dist-packages/jsonschema/compat.py:6: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated since Python 3.3,and in 3.9 it will stop working
  from collections import MutableMapping, Sequence  # noqa
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE

##**UPLOAD**
de arquivos (radar_db e stop_words)


In [3]:
from google.colab import files
df_upload = files.upload()

Saving radar_db to radar_db


In [4]:
stop_words_upload = files.upload()

Saving stopwords.csv to stopwords.csv


In [5]:
stop_words_comum_upload = files.upload()


Saving frequency_stopwords_list.csv to frequency_stopwords_list.csv


In [ ]:
#useless
# processed_docs_upload = files.upload()

##**PREPROCESS** functions

In [6]:
def get_decretos():
  conn = sqlite3.connect('radar_db')
  c = conn.cursor()
  c.execute("SELECT cod_ident_ato, ementa, full_text, referenda FROM Decretos")
  decretos = c.fetchall()
  decretos = [(decreto[0], str(decreto[1]) + " " + str(decreto[2]), decreto[3]) for decreto in decretos]
  conn.close()
  for i in range(len(decretos)):
        referenda_aux = [ref.strip() for ref in decretos[i][2].split(";")]
        decretos[i] = list(decretos[i])
        decretos[i][2] = referenda_aux
        decretos[i] = tuple(decretos[i])
  decretos = pd.DataFrame(decretos)
  decretos.columns = ['cod_ident_ato', 'full_text', 'referenda']
  return decretos

def get_ementa():
  conn = sqlite3.connect('radar_db')
  c = conn.cursor()
  c.execute("SELECT ementa FROM Decretos")
  decretos = c.fetchall()
  # decretos = [(decreto[0], str(decreto[1]) + " " + str(decreto[2]), decreto[3]) for decreto in decretos]
  conn.close()
  return decretos

def preprocess_full(decretos_df):
  number_of_decrees = len(decretos_df['full_text'])
  breaking_punctuation = ['.', '!', '?', ';', ':']
  for j,decreto in enumerate(decretos_df['full_text']):
      print("Preprocessing", j+1, "/", number_of_decrees)
      text = ""
      
      decreto = decreto.replace("/", " ")
      decreto = decreto.replace("º", '')
      tokenized_document = word_tokenize(decreto)
      for i, word in enumerate(tokenized_document):
          
          if word.lower() == "art":               # lidando com os padrões de numeração de artigos definidos na observação.
              if tokenized_document[i+2].isnumeric() and tokenized_document[i+3] == ".":
                  tokenized_document[i+3] = ' '
      
          if(word.isalpha() or word.isnumeric()):
              text+=(word.lower()+" ")
          elif word in breaking_punctuation:
              text+=(" . ")                       # padroniza pontuações específicas em ponto final.
          elif word[0].isnumeric() and ("," not in word):
              word = word.replace(".", "")
              if(word.isnumeric()):
                  text+=(word+" ")                # lidando com números com pontuação no meio. Desconsidera números reais, comumente referentes à moeda.
      
      text = text.replace("art  .", " art ")
      text = text.replace("arts  .", " arts ")
      
      # remoção de assinaturas
      if(text.rfind(" república") != -1):
          signature = text.rfind(" república")
          if signature < len(text)/2:
              signature = len(text)
      
      decretos_df['full_text'].iloc[j] = text[:signature] + " república."
  return decretos_df

def preprocess_ementa(decretos_df):
  number_of_decrees = len(decretos_df['ementa'])
  breaking_punctuation = ['.', '!', '?', ';', ':',]
  for j,decreto in enumerate(decretos_df['ementa']):
      print("Preprocessing", j+1, "/", number_of_decrees)
      text = ""
      
      decreto = decreto.replace("/", " ")
      decreto = decreto.replace("º", '')
      tokenized_document = word_tokenize(decreto)
      for i, word in enumerate(tokenized_document):
          
          if word.lower() == "art":               # lidando com os padrões de numeração de artigos definidos na observação.
              if tokenized_document[i+2].isnumeric() and tokenized_document[i+3] == ".":
                  tokenized_document[i+3] = ' '
      
          if(word.isalpha() or word.isnumeric()):
              text+=(word.lower()+" ")
          elif word in breaking_punctuation:
              text+=(" . ")                       # padroniza pontuações específicas em ponto final.
          elif word[0].isnumeric() and ("," not in word):
              word = word.replace(".", "")
              if(word.isnumeric()):
                  text+=(word+" ")                # lidando com números com pontuação no meio. Desconsidera números reais, comumente referentes à moeda.
      
      text = text.replace("art  .", " art ")
      text = text.replace("arts  .", " arts ")
      
      # remoção de assinaturas
      if(text.rfind(" república") != -1):
          signature = text.rfind(" república")
          if signature < len(text)/2:
              signature = len(text)
      
      decretos_df['ementa'].iloc[j] = text
  return decretos_df

def remove_frequency_stopwords(stopwords_file, docs):
    words=pd.read_csv(stopwords_file, sep=',')
    words = words['0']
    words_list=words.values.tolist()
    
    list_stopwords=[]
    for stop_w in words_list:
        if stop_w[3]==1:
            list_stopwords.append(stop_w[0])

    words_filtered = []
    for doc in docs:
        aux_frequency = ""
        for word in doc.split(" "):
            if word not in list_stopwords:
                aux_frequency+=(word+" ")
        words_filtered.append(aux_frequency)
    return words_filtered

def removeStopWords(stopwords_file,texts, st= stopwords.words('portuguese')):
    frequency_stopwords=pd.read_csv(stopwords_file, sep=',')
    frequency_stopwords = frequency_stopwords['0']
    frequency_stopwords=frequency_stopwords.values.tolist()
    frequency_stopwords.append('janeiro')
    frequency_stopwords.append('fevereiero')
    frequency_stopwords.append('março')
    frequency_stopwords.append('abril')
    frequency_stopwords.append('maio')
    frequency_stopwords.append('junho')
    frequency_stopwords.append('julho')
    frequency_stopwords.append('agosto')
    frequency_stopwords.append('agostar')
    frequency_stopwords.append('setembro')
    frequency_stopwords.append('outubro')
    frequency_stopwords.append('novembro')
    frequency_stopwords.append('dezembro')
    texts_r = []
    for t in texts:
        final_t = ""
        for w in t.split(" "):
            if w not in st and w not in frequency_stopwords and w!=".":
                final_t += w + " "
        texts_r.append(final_t)
    return texts_r

def removeComumStopWords(stopwords_file,texts, st= stopwords.words('portuguese')):
    frequency_stopwords=pd.read_csv(stopwords_file)
    # frequency_stopwords = frequency_stopwords['0']
    frequency_stopwords=frequency_stopwords.values.tolist()
    texts_r = []
    
    for t in texts:
        final_t = ""
        for w in t.split(" "):
            if w not in st and w not in frequency_stopwords and w!=".":
                final_t += w + " "
        texts_r.append(final_t)
    return texts_r

def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']): #'NOUN', 'ADJ', 'VERB', 'ADV'
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append(" ".join([token.lemma_ if token.lemma_ not in ['-PRON-'] else '' for token in doc if token.pos_ in allowed_postags]))
    return texts_out



##**Estrutura** inicial

In [7]:
decretos = get_decretos() #get decress from data base
decretos['ementa'] = pd.DataFrame(get_ementa())
decretos = decretos.drop(columns = ['cod_ident_ato','referenda'], axis=1)
stop_words = pd.read_csv(io.BytesIO(stop_words_upload['stopwords.csv']), sep=',') #set df of stop_words
decretos.head()

full_text                                             ementa
0  Dispõe sobre o Comitê Consultivo de Nanotecnol...  Dispõe sobre o Comitê Consultivo de Nanotecnol...
1  Altera o  Decreto nº 8.642 , de 19 de janeiro ...  Altera o  Decreto nº 8.642 , de 19 de janeiro ...
2  Promulga o Acordo entre o Governo da República...  Promulga o Acordo entre o Governo da República...
3  Promulga o Acordo entre o Governo da República...  Promulga o Acordo entre o Governo da República...
4  Dispõe sobre o Comitê Interministerial de Tecn...  Dispõe sobre o Comitê Interministerial de Tecn...

In [8]:
stop_words

Unnamed: 0      Word  Qtd_total  Qtd_interdocumental  stopword
0               0       NaN     289627                 5294         0
1               1       art      63400                 5294         1
2               2  decretar      41258                 5294         1
3               3         n      37251                 5112         1
4               4       ser      35473                 3905         1
...           ...       ...        ...                  ...       ...
24350       24350     99656          1                    1         0
24351       24351      1888          1                    1         0
24352       24352      3154          1                    1         0
24353       24353      3222          1                    1         0
24354       24354      3310          1                    1         0

[24355 rows x 5 columns]

##**Ementa** analysis

In [9]:
# # decretos = decretos.sample(100)
# ementa_preprocessed = []
# for i in range(len(decretos)):
#     ementa_preprocessed.append(preprocess(decretos.values[i][1], i+1, len(decretos)))
aux = preprocess_ementa(decretos)
ementa_preprocessed = aux['ementa']


A saída de streaming foi truncada nas últimas 5000 linhas.
Preprocessing 1842 / 6841
Preprocessing 1843 / 6841
Preprocessing 1844 / 6841
Preprocessing 1845 / 6841
Preprocessing 1846 / 6841
Preprocessing 1847 / 6841
Preprocessing 1848 / 6841
Preprocessing 1849 / 6841
Preprocessing 1850 / 6841
Preprocessing 1851 / 6841
Preprocessing 1852 / 6841
Preprocessing 1853 / 6841
Preprocessing 1854 / 6841
Preprocessing 1855 / 6841
Preprocessing 1856 / 6841
Preprocessing 1857 / 6841
Preprocessing 1858 / 6841
Preprocessing 1859 / 6841
Preprocessing 1860 / 6841
Preprocessing 1861 / 6841
Preprocessing 1862 / 6841
Preprocessing 1863 / 6841
Preprocessing 1864 / 6841
Preprocessing 1865 / 6841
Preprocessing 1866 / 6841
Preprocessing 1867 / 6841
Preprocessing 1868 / 6841
Preprocessing 1869 / 6841
Preprocessing 1870 / 6841
Preprocessing 1871 / 6841
Preprocessing 1872 / 6841
Preprocessing 1873 / 6841
Preprocessing 1874 / 6841
Preprocessing 1875 / 6841
Preprocessing 1876 / 6841
Preprocessing 1877 / 6841
Prepr

In [10]:
ementa_preprocessed = ementa_preprocessed.values.tolist()

In [11]:
ementa_preprocessed[1]

'altera o decreto n 8642 de 19 de janeiro de 2016 que dispõe sobre a autoridade pública de governança do futebol apfut criada pela lei n 13155 de 4 de agosto de 2015  . '

In [12]:
ementa_processed = removeStopWords("frequency_stopwords_list.csv",ementa_preprocessed)
ementa_processed = removeComumStopWords("stopwords.csv",ementa_preprocessed)
# ementa_processed = removeStopWords("stopwords.csv",ementa_preprocessed)

In [13]:
ementa_processed_docs = [doc.split(" ") for doc in ementa_processed]

# Do lemmatization keeping only Noun, Adj, Verb, Adverb
data_lemmatized = lemmatization(ementa_processed_docs, allowed_postags=['NOUN', 'ADJ']) #select noun and verb
print(data_lemmatized[:2])

A saída de streaming foi truncada nas últimas 5000 linhas.
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarni

['comitê consultivo novo material âmbito tecnologia', 'decretar n janeiro autoridade público futebol lei agostar']


/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use sele

In [14]:
splited_doc = [doc.split(" ") for doc in data_lemmatized]
splited_doc[1]

['decretar',
 'n',
 'janeiro',
 'autoridade',
 'público',
 'futebol',
 'lei',
 'agostar']

In [15]:
# ementa_preprocessed_docs = ementa_preprocessed.values.tolist()

ementa_dictionary = gensim.corpora.Dictionary(splited_doc)

non_filtering = ementa_dictionary
ementa_dictionary.filter_extremes(no_below=3, no_above=0.8) #keep_n=10000)

INFO : adding document #0 to Dictionary(0 unique tokens: [])
INFO : built Dictionary(2763 unique tokens: ['comitê', 'consultivo', 'material', 'novo', 'tecnologia']...) from 6841 documents (total 53276 corpus positions)
INFO : discarding 1356 tokens: [('assistiva', 1), ('primário', 1), ('secundário', 1), ('esporte', 1), ('sucroalcooleiro', 2), ('participar', 1), ('eletrobras', 1), ('café', 2), ('instância', 2), ('entrar', 2)]...
INFO : keeping 1407 tokens which were in no less than 3 and no more than 5472 (=80.0%) documents
INFO : resulting dictionary: Dictionary(1407 unique tokens: ['comitê', 'consultivo', 'material', 'novo', 'tecnologia']...)


In [16]:
bow_corpus = [ementa_dictionary.doc2bow(doc) for doc in splited_doc]

n_topics = 10
lda_model = gensim.models.LdaModel(bow_corpus, num_topics=n_topics, id2word=ementa_dictionary, passes=30, alpha='auto', random_state=42)

A saída de streaming foi truncada nas últimas 5000 linhas.
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np

In [17]:
for idx, topic in lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

INFO : topic #0 (0.080): 0.056*"executivo" + 0.055*"financeiro" + 0.049*"poder" + 0.040*"exercício" + 0.038*"execução" + 0.034*"providência" + 0.033*"orçamentária" + 0.029*"programação" + 0.025*"sanção" + 0.025*"decretar"
INFO : topic #1 (0.227): 0.102*"decretar" + 0.058*"regulamentar" + 0.055*"lei" + 0.046*"n" + 0.029*"providência" + 0.024*"dezembro" + 0.022*"outubro" + 0.022*"julho" + 0.021*"maio" + 0.020*"janeiro"
INFO : topic #2 (0.083): 0.134*"redação" + 0.126*"novo" + 0.056*"decretar" + 0.043*"competência" + 0.026*"ministrar" + 0.019*"assistência" + 0.018*"gestão" + 0.018*"atos" + 0.016*"direito" + 0.014*"comissão"
INFO : topic #3 (0.048): 0.053*"oficiar" + 0.042*"produto" + 0.040*"promoção" + 0.036*"impor" + 0.034*"incidência" + 0.034*"tempo" + 0.031*"dezembro" + 0.030*"decretar" + 0.027*"efetivos" + 0.024*"obrigatório"
INFO : topic #4 (0.129): 0.131*"providência" + 0.088*"social" + 0.077*"nacional" + 0.031*"brasileiro" + 0.030*"remanejamento" + 0.027*"conselho" + 0.025*"estatut

Topic: 0 
Words: 0.056*"executivo" + 0.055*"financeiro" + 0.049*"poder" + 0.040*"exercício" + 0.038*"execução" + 0.034*"providência" + 0.033*"orçamentária" + 0.029*"programação" + 0.025*"sanção" + 0.025*"decretar"
Topic: 1 
Words: 0.102*"decretar" + 0.058*"regulamentar" + 0.055*"lei" + 0.046*"n" + 0.029*"providência" + 0.024*"dezembro" + 0.022*"outubro" + 0.022*"julho" + 0.021*"maio" + 0.020*"janeiro"
Topic: 2 
Words: 0.134*"redação" + 0.126*"novo" + 0.056*"decretar" + 0.043*"competência" + 0.026*"ministrar" + 0.019*"assistência" + 0.018*"gestão" + 0.018*"atos" + 0.016*"direito" + 0.014*"comissão"
Topic: 3 
Words: 0.053*"oficiar" + 0.042*"produto" + 0.040*"promoção" + 0.036*"impor" + 0.034*"incidência" + 0.034*"tempo" + 0.031*"dezembro" + 0.030*"decretar" + 0.027*"efetivos" + 0.024*"obrigatório"
Topic: 4 
Words: 0.131*"providência" + 0.088*"social" + 0.077*"nacional" + 0.031*"brasileiro" + 0.030*"remanejamento" + 0.027*"conselho" + 0.025*"estatuto" + 0.023*"sistema" + 0.022*"assessoram

In [18]:
#Print the Keyword in the 10 topics
pprint(lda_model.print_topics())
doc_lda = lda_model[bow_corpus]

INFO : topic #0 (0.080): 0.056*"executivo" + 0.055*"financeiro" + 0.049*"poder" + 0.040*"exercício" + 0.038*"execução" + 0.034*"providência" + 0.033*"orçamentária" + 0.029*"programação" + 0.025*"sanção" + 0.025*"decretar"
INFO : topic #1 (0.227): 0.102*"decretar" + 0.058*"regulamentar" + 0.055*"lei" + 0.046*"n" + 0.029*"providência" + 0.024*"dezembro" + 0.022*"outubro" + 0.022*"julho" + 0.021*"maio" + 0.020*"janeiro"
INFO : topic #2 (0.083): 0.134*"redação" + 0.126*"novo" + 0.056*"decretar" + 0.043*"competência" + 0.026*"ministrar" + 0.019*"assistência" + 0.018*"gestão" + 0.018*"atos" + 0.016*"direito" + 0.014*"comissão"
INFO : topic #3 (0.048): 0.053*"oficiar" + 0.042*"produto" + 0.040*"promoção" + 0.036*"impor" + 0.034*"incidência" + 0.034*"tempo" + 0.031*"dezembro" + 0.030*"decretar" + 0.027*"efetivos" + 0.024*"obrigatório"
INFO : topic #4 (0.129): 0.131*"providência" + 0.088*"social" + 0.077*"nacional" + 0.031*"brasileiro" + 0.030*"remanejamento" + 0.027*"conselho" + 0.025*"estatut

[(0,
  '0.056*"executivo" + 0.055*"financeiro" + 0.049*"poder" + 0.040*"exercício" '
  '+ 0.038*"execução" + 0.034*"providência" + 0.033*"orçamentária" + '
  '0.029*"programação" + 0.025*"sanção" + 0.025*"decretar"'),
 (1,
  '0.102*"decretar" + 0.058*"regulamentar" + 0.055*"lei" + 0.046*"n" + '
  '0.029*"providência" + 0.024*"dezembro" + 0.022*"outubro" + 0.022*"julho" + '
  '0.021*"maio" + 0.020*"janeiro"'),
 (2,
  '0.134*"redação" + 0.126*"novo" + 0.056*"decretar" + 0.043*"competência" + '
  '0.026*"ministrar" + 0.019*"assistência" + 0.018*"gestão" + 0.018*"atos" + '
  '0.016*"direito" + 0.014*"comissão"'),
 (3,
  '0.053*"oficiar" + 0.042*"produto" + 0.040*"promoção" + 0.036*"impor" + '
  '0.034*"incidência" + 0.034*"tempo" + 0.031*"dezembro" + 0.030*"decretar" + '
  '0.027*"efetivos" + 0.024*"obrigatório"'),
 (4,
  '0.131*"providência" + 0.088*"social" + 0.077*"nacional" + '
  '0.031*"brasileiro" + 0.030*"remanejamento" + 0.027*"conselho" + '
  '0.025*"estatuto" + 0.023*"sistema" + 

##**Validation** ementa

In [19]:
from sklearn.feature_extraction.text import CountVectorizer#, TfidfVectorizer


In [20]:
#Create the Document-Word matrix
vectorizer = CountVectorizer(analyzer='word',       
                             min_df=3,
# minimum reqd occurences of a word 
                             stop_words='english',             
# remove stop words
                             lowercase=True,                   
# convert all words to lowercase
                             token_pattern='[a-zA-Z0-9]{3,}',  
# num chars > 3
                             # max_features=50000,             
# max number of uniq words   
                              )

data_vectorized = vectorizer.fit_transform(data_lemmatized)


In [21]:
from sklearn.decomposition import LatentDirichletAllocation

In [22]:
# Build LDA Model
lda_model = LatentDirichletAllocation(n_components=20,               # Number of topics
                                      max_iter=10,               
# Max learning iterations
                                      learning_method='online',   
                                      random_state=100,          
# Random state
                                      batch_size=128,            
# n docs in each learning iter
                                      evaluate_every = -1,       
# compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               
# Use all available CPUs
                                     )
                                     
lda_output = lda_model.fit_transform(data_vectorized)
print(lda_model)  # Model attributes

LatentDirichletAllocation(batch_size=128, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=20, n_jobs=-1,
                          perp_tol=0.1, random_state=100, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)


In [23]:
# Log Likelyhood: Higher the better
print("Log Likelihood: ", lda_model.score(data_vectorized))
# Perplexity: Lower the better. Perplexity = exp(-1. * log-likelihood per word)
print("Perplexity: ", lda_model.perplexity(data_vectorized))
# See model parameters
pprint(lda_model.get_params())

Log Likelihood:  -330753.38425145246
Perplexity:  326.97778820513145
{'batch_size': 128,
 'doc_topic_prior': None,
 'evaluate_every': -1,
 'learning_decay': 0.7,
 'learning_method': 'online',
 'learning_offset': 10.0,
 'max_doc_update_iter': 100,
 'max_iter': 10,
 'mean_change_tol': 0.001,
 'n_components': 20,
 'n_jobs': -1,
 'perp_tol': 0.1,
 'random_state': 100,
 'topic_word_prior': None,
 'total_samples': 1000000.0,
 'verbose': 0}


In [24]:
from sklearn.model_selection import GridSearchCV

In [25]:
# Define Search Param
search_params = {'n_components': [10, 15, 20, 25, 30], 'learning_decay': [.5, .7, .9]}
# Init the Model
lda = LatentDirichletAllocation(max_iter=5, learning_method='online', learning_offset=50.,random_state=0)
# Init Grid Search Class
model = GridSearchCV(lda, param_grid=search_params)
# Do the Grid Search
model.fit(data_vectorized)

GridSearchCV(cv=None, error_score=nan,
             estimator=LatentDirichletAllocation(batch_size=128,
                                                 doc_topic_prior=None,
                                                 evaluate_every=-1,
                                                 learning_decay=0.7,
                                                 learning_method='online',
                                                 learning_offset=50.0,
                                                 max_doc_update_iter=100,
                                                 max_iter=5,
                                                 mean_change_tol=0.001,
                                                 n_components=10, n_jobs=None,
                                                 perp_tol=0.1, random_state=0,
                                                 topic_word_prior=None,
                                                 total_samples=1000000.0,
                               

In [26]:
# Best Model
best_lda_model = model.best_estimator_
# Model Parameters
print("Best Model's Params: ", model.best_params_)
# Log Likelihood Score
print("Best Log Likelihood Score: ", model.best_score_)
# Perplexity
print("Model Perplexity: ", best_lda_model.perplexity(data_vectorized))

Best Model's Params:  {'learning_decay': 0.7, 'n_components': 10}
Best Log Likelihood Score:  -74073.15713574142
Model Perplexity:  276.78943134745987


##**Visualisation** ementa

In [27]:
# Create Document — Topic Matrix
lda_output = best_lda_model.transform(data_vectorized)
# column names
topicnames = ["Topic" + str(i) for i in range(best_lda_model.n_components)]
# index names
docnames = ["Doc" + str(i) for i in range(len(ementa_processed_docs))]
# Make the pandas dataframe
df_document_topic = pd.DataFrame(np.round(lda_output, 2), columns=topicnames, index=docnames)
# Get dominant topic for each document
dominant_topic = np.argmax(df_document_topic.values, axis=1)
df_document_topic['dominant_topic'] = dominant_topic
# Styling
def color_green(val):
 color = 'green' if val > .1 else 'black'
 return 'color: {col}'.format(col=color)
def make_bold(val):
 weight = 700 if val > .1 else 400
 return 'font-weight: {weight}'.format(weight=weight)
# Apply Style
df_document_topics = df_document_topic.head(15).style.applymap(color_green).applymap(make_bold)
df_document_topics

In [28]:
# Topic-Keyword Matrix
df_topic_keywords = pd.DataFrame(best_lda_model.components_)
# Assign Column and Index
df_topic_keywords.columns = vectorizer.get_feature_names()
df_topic_keywords.index = topicnames
# View
df_topic_keywords.head()

1979      1980      1987  ...    zagreb     zonar  zoneamento
Topic0  0.100313  0.100271  0.100316  ...  0.113878  0.100614    0.100271
Topic1  0.100231  0.100227  0.100267  ...  0.100292  0.100386    0.100271
Topic2  0.100264  0.100282  0.100450  ...  0.100258  0.100283    0.100250
Topic3  0.100275  0.100295  0.100296  ...  0.100268  6.307909    0.100279
Topic4  0.100248  0.100296  0.100970  ...  3.922823  7.156623    0.100266

[5 rows x 1414 columns]

In [29]:
lda_model_n = gensim.models.LdaModel(bow_corpus, num_topics=n_topics, id2word=ementa_dictionary, passes=30, alpha='auto', random_state=42)

A saída de streaming foi truncada nas últimas 5000 linhas.
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np

In [30]:
from pprint import pprint

# Print the Keyword in the 10 topics
pprint(lda_model_n.print_topics())
doc_lda = lda_model_n[bow_corpus]

INFO : topic #0 (0.080): 0.056*"executivo" + 0.055*"financeiro" + 0.049*"poder" + 0.040*"exercício" + 0.038*"execução" + 0.034*"providência" + 0.033*"orçamentária" + 0.029*"programação" + 0.025*"sanção" + 0.025*"decretar"
INFO : topic #1 (0.227): 0.102*"decretar" + 0.058*"regulamentar" + 0.055*"lei" + 0.046*"n" + 0.029*"providência" + 0.024*"dezembro" + 0.022*"outubro" + 0.022*"julho" + 0.021*"maio" + 0.020*"janeiro"
INFO : topic #2 (0.083): 0.134*"redação" + 0.126*"novo" + 0.056*"decretar" + 0.043*"competência" + 0.026*"ministrar" + 0.019*"assistência" + 0.018*"gestão" + 0.018*"atos" + 0.016*"direito" + 0.014*"comissão"
INFO : topic #3 (0.048): 0.053*"oficiar" + 0.042*"produto" + 0.040*"promoção" + 0.036*"impor" + 0.034*"incidência" + 0.034*"tempo" + 0.031*"dezembro" + 0.030*"decretar" + 0.027*"efetivos" + 0.024*"obrigatório"
INFO : topic #4 (0.129): 0.131*"providência" + 0.088*"social" + 0.077*"nacional" + 0.031*"brasileiro" + 0.030*"remanejamento" + 0.027*"conselho" + 0.025*"estatut

[(0,
  '0.056*"executivo" + 0.055*"financeiro" + 0.049*"poder" + 0.040*"exercício" '
  '+ 0.038*"execução" + 0.034*"providência" + 0.033*"orçamentária" + '
  '0.029*"programação" + 0.025*"sanção" + 0.025*"decretar"'),
 (1,
  '0.102*"decretar" + 0.058*"regulamentar" + 0.055*"lei" + 0.046*"n" + '
  '0.029*"providência" + 0.024*"dezembro" + 0.022*"outubro" + 0.022*"julho" + '
  '0.021*"maio" + 0.020*"janeiro"'),
 (2,
  '0.134*"redação" + 0.126*"novo" + 0.056*"decretar" + 0.043*"competência" + '
  '0.026*"ministrar" + 0.019*"assistência" + 0.018*"gestão" + 0.018*"atos" + '
  '0.016*"direito" + 0.014*"comissão"'),
 (3,
  '0.053*"oficiar" + 0.042*"produto" + 0.040*"promoção" + 0.036*"impor" + '
  '0.034*"incidência" + 0.034*"tempo" + 0.031*"dezembro" + 0.030*"decretar" + '
  '0.027*"efetivos" + 0.024*"obrigatório"'),
 (4,
  '0.131*"providência" + 0.088*"social" + 0.077*"nacional" + '
  '0.031*"brasileiro" + 0.030*"remanejamento" + 0.027*"conselho" + '
  '0.025*"estatuto" + 0.023*"sistema" + 

In [31]:
pyLDAvis.enable_notebook()
LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model_n, bow_corpus, ementa_dictionary)
LDAvis_prepared

INFO : NumExpr defaulting to 2 threads.


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
1     -0.002585  0.107394       1        1  21.914713
7     -0.160733 -0.172464       2        1  14.146303
5     -0.045318  0.213980       3        1   9.990867
6     -0.101172 -0.008725       4        1   9.278004
4     -0.255364 -0.124765       5        1   9.005428
8      0.203424 -0.053556       6        1   8.610385
9      0.307995 -0.214062       7        1   8.132752
0     -0.056845 -0.098562       8        1   7.893897
2      0.032024  0.146669       9        1   6.517197
3      0.078573  0.204090      10        1   4.510455, topic_info=           Term        Freq        Total Category  logprob  loglift
104       cargo  991.000000   991.000000  Default  30.0000  30.0000
70       função  983.000000   983.000000  Default  29.0000  29.0000
105  estruturar  711.000000   711.000000  Default  28.0000  28.0000
106  regimental  635.000000   635.000000  Default  27.0000  27.0000
949     redação  450.000000   450.000000  Default  26.0000  26.0000
..          ...         ...          ...      ...      ...      ...
18      serviço   45.784536   327.411375  Topic10  -3.9263   1.1315
168      efeito   23.121436    43.861287  Topic10  -4.6095   2.4585
8      decretar   69.318471  1882.124480  Topic10  -3.5115  -0.2027
335      anexar   31.200339   227.945172  Topic10  -4.3098   1.1101
12            n   30.121786   704.248168  Topic10  -4.3450  -0.0531

[527 rows x 6 columns], token_table=      Topic      Freq   Term
term                        
116       5  0.980543       
1354      7  0.958664      2
316       1  0.333421   2000
316       8  0.652346   2000
1103      1  0.980428   2001
...     ...       ...    ...
693       2  0.107164  órgão
693       5  0.300059  órgão
693       8  0.589402  órgão
211       1  0.855700  único
211       4  0.133109  único

[664 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[2, 8, 6, 7, 5, 9, 10, 1, 3, 4])

##**FULL_TEXT** analysis

In [32]:
full_text_preprocessed = preprocess_full(aux)
full_text_preprocessed = full_text_preprocessed['full_text'].values.tolist()

A saída de streaming foi truncada nas últimas 5000 linhas.
Preprocessing 1842 / 6841
Preprocessing 1843 / 6841
Preprocessing 1844 / 6841
Preprocessing 1845 / 6841
Preprocessing 1846 / 6841
Preprocessing 1847 / 6841
Preprocessing 1848 / 6841
Preprocessing 1849 / 6841
Preprocessing 1850 / 6841
Preprocessing 1851 / 6841
Preprocessing 1852 / 6841
Preprocessing 1853 / 6841
Preprocessing 1854 / 6841
Preprocessing 1855 / 6841
Preprocessing 1856 / 6841
Preprocessing 1857 / 6841
Preprocessing 1858 / 6841
Preprocessing 1859 / 6841
Preprocessing 1860 / 6841
Preprocessing 1861 / 6841
Preprocessing 1862 / 6841
Preprocessing 1863 / 6841
Preprocessing 1864 / 6841
Preprocessing 1865 / 6841
Preprocessing 1866 / 6841
Preprocessing 1867 / 6841
Preprocessing 1868 / 6841
Preprocessing 1869 / 6841
Preprocessing 1870 / 6841
Preprocessing 1871 / 6841
Preprocessing 1872 / 6841
Preprocessing 1873 / 6841
Preprocessing 1874 / 6841
Preprocessing 1875 / 6841
Preprocessing 1876 / 6841
Preprocessing 1877 / 6841
Prepr

In [34]:
full_text_processed = removeComumStopWords("stopwords.csv",full_text_preprocessed)

In [35]:
full_text_processed = removeStopWords("frequency_stopwords_list.csv",full_text_processed)
full_text_processed_docs = [doc.split(" ") for doc in full_text_processed]


In [36]:
# Do lemmatization keeping only Noun, Adj, Verb, Adverb
data_lemmatized_full = lemmatization(full_text_processed_docs, allowed_postags=['NOUN', 'ADJ']) #select noun and verb
print(data_lemmatized_full[:2])

A saída de streaming foi truncada nas últimas 5000 linhas.
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarni

['comitê consultivo novo material âmbito tecnologia atribuição conferir decretar comitê consultivo novo material âmbito tecnologia comitê consultivo nanotecnologia novo material órgão assessoramento proposto temático nanotecnologias novo material área prioritário alocação recurso avaliação iniciativo ações programar projetos comitê consultivo nanotecnologia novo material representante seguinte órgão entidade tecnologia físico cbpf c desenvolvimento científico tecnológico financiador estudo projetos finep aperfeiçoamento pessoal nível centrar energia econômico social h petróleo brasileiro notório área nanotecnologia novo material organização sociedade civil entidade classe similar membro consultivo nanotecnologia novo material ausência impedimento consultivo novo material respectivo suplente titular órgão entidade ministrar tecnologia consultivo novo material respectivo suplente ministrar tecnologia inovação mandatar renovável igual período membro consultivo novo material respectivo sup

/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  for entry_point in AVAILABLE_ENTRY_POINTS.get(self.entry_point_namespace, []):
/usr/local/lib/python3.7/dist-packages/catalogue.py:138: DeprecationWarning: SelectableGroups dict interface is deprecated. Use sele

In [37]:
full_text_splited_doc = [doc.split(" ") for doc in data_lemmatized_full]
full_text_splited_doc[1]

['decretar',
 'autoridade',
 'público',
 'futebol',
 'lei',
 'atribuição',
 'inciso',
 'lei',
 'decretar',
 'seguinte',
 'alteração',
 'autoridade',
 'público',
 'futebol',
 'apfut',
 'órgão',
 '2015',
 'âmbito',
 'finalidade',
 'cumprimentar',
 'condição',
 'manutenção',
 'modernização',
 'gestão',
 'responsabilidade',
 'fiscal',
 'futebol',
 'brasileiro',
 'plenário',
 'seguinte',
 'representante',
 'especial',
 'esporte',
 'repúblico',
 'atleta',
 'futebol',
 'profissional',
 'dirigente',
 'futebol',
 'profissional',
 'futebol',
 'profissional',
 'futebol',
 'profissional',
 'entidade',
 'desenvolvimento',
 'futebol',
 'brasileiro',
 'apfut',
 'ministrar',
 'artigo',
 'ausência',
 'impedimento',
 'respectivo',
 'suplente',
 'inciso',
 'ir',
 'titular',
 'órgão',
 'secretário',
 'especial',
 'suplente',
 'secretário',
 'especial',
 'inciso',
 'função',
 'membro',
 'atribuição',
 'regular',
 'órgão',
 'origem',
 'inciso',
 'suplente',
 'secretário',
 'especial',
 'indicação',
 'consel

In [38]:
# processed_docs = [doc.split(" ") for doc in processed_docs]
dictionary = gensim.corpora.Dictionary(full_text_splited_doc)

non_filtering_full = dictionary
dictionary.filter_extremes(no_below=3, no_above=0.8) #keep_n=10000)

INFO : adding document #0 to Dictionary(0 unique tokens: [])
INFO : built Dictionary(12707 unique tokens: ['absoluto', 'alocação', 'ano', 'aperfeiçoamento', 'aprovação']...) from 6841 documents (total 1267300 corpus positions)
INFO : discarding 6227 tokens: [('atribuição', 6810), ('cbpf', 1), ('datar', 6715), ('decretar', 6830), ('nanotecnologia', 1), ('nanotecnologias', 2), ('7857', 1), ('ccl', 2), ('ccxxv', 2), ('ccxxxvi', 1)]...
INFO : keeping 6480 tokens which were in no less than 3 and no more than 5472 (=80.0%) documents
INFO : resulting dictionary: Dictionary(6480 unique tokens: ['absoluto', 'alocação', 'ano', 'aperfeiçoamento', 'aprovação']...)


In [39]:
bow_corpus_full = [dictionary.doc2bow(doc) for doc in full_text_splited_doc]

n_topics = 10
lda_model_full = gensim.models.LdaModel(bow_corpus_full, num_topics=n_topics, id2word=dictionary, passes=30, alpha='auto', random_state=42)

A saída de streaming foi truncada nas últimas 5000 linhas.
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np

In [40]:
for idx, topic in lda_model_full.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))

INFO : topic #0 (0.035): 0.027*"instituição" + 0.017*"ensinar" + 0.015*"profissional" + 0.015*"curso" + 0.011*"autorização" + 0.008*"formação" + 0.008*"superior" + 0.008*"avaliação" + 0.008*"genético" + 0.007*"atividades"
INFO : topic #1 (0.074): 0.027*"lei" + 0.020*"militar" + 0.019*"financeiro" + 0.017*"despesa" + 0.015*"órgão" + 0.014*"recurso" + 0.012*"anexar" + 0.011*"oficiar" + 0.011*"redação" + 0.011*"exercício"
INFO : topic #2 (0.041): 0.050*"produto" + 0.012*"elétrica" + 0.012*"estabelecimento" + 0.011*"energia" + 0.008*"produção" + 0.007*"infração" + 0.006*"órgão" + 0.006*"lei" + 0.006*"técnico" + 0.006*"embalagem"
INFO : topic #3 (0.078): 0.022*"público" + 0.019*"órgão" + 0.014*"desenvolvimento" + 0.014*"conselho" + 0.013*"representante" + 0.013*"atividades" + 0.013*"político" + 0.012*"entidade" + 0.011*"ações" + 0.010*"redação"
INFO : topic #4 (0.042): 0.029*"lei" + 0.017*"pessoa" + 0.015*"jurídico" + 0.014*"fiscal" + 0.013*"pontar" + 0.013*"redação" + 0.010*"regime" + 0.01

Topic: 0 
Words: 0.027*"instituição" + 0.017*"ensinar" + 0.015*"profissional" + 0.015*"curso" + 0.011*"autorização" + 0.008*"formação" + 0.008*"superior" + 0.008*"avaliação" + 0.008*"genético" + 0.007*"atividades"
Topic: 1 
Words: 0.027*"lei" + 0.020*"militar" + 0.019*"financeiro" + 0.017*"despesa" + 0.015*"órgão" + 0.014*"recurso" + 0.012*"anexar" + 0.011*"oficiar" + 0.011*"redação" + 0.011*"exercício"
Topic: 2 
Words: 0.050*"produto" + 0.012*"elétrica" + 0.012*"estabelecimento" + 0.011*"energia" + 0.008*"produção" + 0.007*"infração" + 0.006*"órgão" + 0.006*"lei" + 0.006*"técnico" + 0.006*"embalagem"
Topic: 3 
Words: 0.022*"público" + 0.019*"órgão" + 0.014*"desenvolvimento" + 0.014*"conselho" + 0.013*"representante" + 0.013*"atividades" + 0.013*"político" + 0.012*"entidade" + 0.011*"ações" + 0.010*"redação"
Topic: 4 
Words: 0.029*"lei" + 0.017*"pessoa" + 0.015*"jurídico" + 0.014*"fiscal" + 0.013*"pontar" + 0.013*"redação" + 0.010*"regime" + 0.010*"importação" + 0.010*"mercadoria" + 0.

In [41]:
#Print the Keyword in the 10 topics
pprint(lda_model_full.print_topics())
doc_lda = lda_model_full[bow_corpus_full]

INFO : topic #0 (0.035): 0.027*"instituição" + 0.017*"ensinar" + 0.015*"profissional" + 0.015*"curso" + 0.011*"autorização" + 0.008*"formação" + 0.008*"superior" + 0.008*"avaliação" + 0.008*"genético" + 0.007*"atividades"
INFO : topic #1 (0.074): 0.027*"lei" + 0.020*"militar" + 0.019*"financeiro" + 0.017*"despesa" + 0.015*"órgão" + 0.014*"recurso" + 0.012*"anexar" + 0.011*"oficiar" + 0.011*"redação" + 0.011*"exercício"
INFO : topic #2 (0.041): 0.050*"produto" + 0.012*"elétrica" + 0.012*"estabelecimento" + 0.011*"energia" + 0.008*"produção" + 0.007*"infração" + 0.006*"órgão" + 0.006*"lei" + 0.006*"técnico" + 0.006*"embalagem"
INFO : topic #3 (0.078): 0.022*"público" + 0.019*"órgão" + 0.014*"desenvolvimento" + 0.014*"conselho" + 0.013*"representante" + 0.013*"atividades" + 0.013*"político" + 0.012*"entidade" + 0.011*"ações" + 0.010*"redação"
INFO : topic #4 (0.042): 0.029*"lei" + 0.017*"pessoa" + 0.015*"jurídico" + 0.014*"fiscal" + 0.013*"pontar" + 0.013*"redação" + 0.010*"regime" + 0.01

[(0,
  '0.027*"instituição" + 0.017*"ensinar" + 0.015*"profissional" + '
  '0.015*"curso" + 0.011*"autorização" + 0.008*"formação" + 0.008*"superior" + '
  '0.008*"avaliação" + 0.008*"genético" + 0.007*"atividades"'),
 (1,
  '0.027*"lei" + 0.020*"militar" + 0.019*"financeiro" + 0.017*"despesa" + '
  '0.015*"órgão" + 0.014*"recurso" + 0.012*"anexar" + 0.011*"oficiar" + '
  '0.011*"redação" + 0.011*"exercício"'),
 (2,
  '0.050*"produto" + 0.012*"elétrica" + 0.012*"estabelecimento" + '
  '0.011*"energia" + 0.008*"produção" + 0.007*"infração" + 0.006*"órgão" + '
  '0.006*"lei" + 0.006*"técnico" + 0.006*"embalagem"'),
 (3,
  '0.022*"público" + 0.019*"órgão" + 0.014*"desenvolvimento" + '
  '0.014*"conselho" + 0.013*"representante" + 0.013*"atividades" + '
  '0.013*"político" + 0.012*"entidade" + 0.011*"ações" + 0.010*"redação"'),
 (4,
  '0.029*"lei" + 0.017*"pessoa" + 0.015*"jurídico" + 0.014*"fiscal" + '
  '0.013*"pontar" + 0.013*"redação" + 0.010*"regime" + 0.010*"importação" + '
  '0.010*

##**FULL_TEXT** validation

In [42]:
# # Do lemmatization keeping only Noun, Adj, Verb, Adverb
# data_lemmatized_full = lemmatization(processed_docs, allowed_postags=['NOUN', 'VERB']) #select noun and verb
# print(data_lemmatized_full[:2])

In [43]:
data_vectorized_full = vectorizer.fit_transform(data_lemmatized_full)
lda_output = lda_model.fit_transform(data_vectorized_full)
print(lda_model)  # Model attributes

LatentDirichletAllocation(batch_size=128, doc_topic_prior=None,
                          evaluate_every=-1, learning_decay=0.7,
                          learning_method='online', learning_offset=10.0,
                          max_doc_update_iter=100, max_iter=10,
                          mean_change_tol=0.001, n_components=20, n_jobs=-1,
                          perp_tol=0.1, random_state=100, topic_word_prior=None,
                          total_samples=1000000.0, verbose=0)


In [44]:
# Log Likelyhood: Higher the better
print("Log Likelihood: ", lda_model.score(data_vectorized_full))
# Perplexity: Lower the better. Perplexity = exp(-1. * log-likelihood per word)
print("Perplexity: ", lda_model.perplexity(data_vectorized_full))
# See model parameters
pprint(lda_model.get_params())

Log Likelihood:  -8620741.130993966
Perplexity:  560.1521329702204
{'batch_size': 128,
 'doc_topic_prior': None,
 'evaluate_every': -1,
 'learning_decay': 0.7,
 'learning_method': 'online',
 'learning_offset': 10.0,
 'max_doc_update_iter': 100,
 'max_iter': 10,
 'mean_change_tol': 0.001,
 'n_components': 20,
 'n_jobs': -1,
 'perp_tol': 0.1,
 'random_state': 100,
 'topic_word_prior': None,
 'total_samples': 1000000.0,
 'verbose': 0}


In [45]:
# Define Search Param
search_params = {'n_components': [5,10, 15, 20, 25, 30], 'learning_decay': [.5, .7, .9]}
# Init the Model
lda = LatentDirichletAllocation(max_iter=5, learning_method='online', learning_offset=50.,random_state=0)
# Init Grid Search Class
model = GridSearchCV(lda, param_grid=search_params)
# Do the Grid Search
model.fit(data_vectorized_full)

GridSearchCV(cv=None, error_score=nan,
             estimator=LatentDirichletAllocation(batch_size=128,
                                                 doc_topic_prior=None,
                                                 evaluate_every=-1,
                                                 learning_decay=0.7,
                                                 learning_method='online',
                                                 learning_offset=50.0,
                                                 max_doc_update_iter=100,
                                                 max_iter=5,
                                                 mean_change_tol=0.001,
                                                 n_components=10, n_jobs=None,
                                                 perp_tol=0.1, random_state=0,
                                                 topic_word_prior=None,
                                                 total_samples=1000000.0,
                               

In [46]:
# Best Model
best_lda_model = model.best_estimator_
# Model Parameters
print("Best Model's Params: ", model.best_params_)
# Log Likelihood Score
print("Best Log Likelihood Score: ", model.best_score_)
# Perplexity
print("Model Perplexity: ", best_lda_model.perplexity(data_vectorized_full))

Best Model's Params:  {'learning_decay': 0.5, 'n_components': 20}
Best Log Likelihood Score:  -1828614.325345143
Model Perplexity:  563.8744563664746


##**FULL_TEXT** visualization

In [47]:
# Create Document — Topic Matrix
lda_output = best_lda_model.transform(data_vectorized_full)
# column names
topicnames = ["Topic" + str(i) for i in range(best_lda_model.n_components)]
# index names
docnames = ["Doc" + str(i) for i in range(len(data_lemmatized_full))]
# Make the pandas dataframe
df_document_topic = pd.DataFrame(np.round(lda_output, 2), columns=topicnames, index=docnames)
# Get dominant topic for each document
dominant_topic = np.argmax(df_document_topic.values, axis=1)
df_document_topic['dominant_topic'] = dominant_topic
# Styling
def color_green(val):
 color = 'green' if val > .1 else 'black'
 return 'color: {col}'.format(col=color)
def make_bold(val):
 weight = 700 if val > .1 else 400
 return 'font-weight: {weight}'.format(weight=weight)
# Apply Style
df_document_topics = df_document_topic.head(15).style.applymap(color_green).applymap(make_bold)
df_document_topics

In [48]:
# Topic-Keyword Matrix
df_topic_keywords = pd.DataFrame(best_lda_model.components_)
# Assign Column and Index
df_topic_keywords.columns = vectorizer.get_feature_names()
df_topic_keywords.index = topicnames
# View
df_topic_keywords.head()

101  1011  1012  1013  ...  zoneamentos  zoossanit  zoot   zpe
Topic0  0.05  0.05  0.05  0.05  ...         0.05       0.05  0.05  0.05
Topic1  0.05  0.05  0.05  0.05  ...         0.05       0.05  0.05  0.05
Topic2  0.05  0.05  0.05  0.05  ...         0.05       0.05  0.05  0.05
Topic3  0.05  0.05  0.05  0.05  ...         0.05       0.05  0.05  0.05
Topic4  0.05  0.05  0.05  0.05  ...         0.05       0.05  0.05  0.05

[5 rows x 6204 columns]

In [49]:
lda_model_n = gensim.models.LdaModel(bow_corpus_full, num_topics=25, id2word=dictionary, passes=30, alpha='auto', random_state=42)

A saída de streaming foi truncada nas últimas 5000 linhas.
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
/usr/local/lib/python3.7/dist-packages/gensim/models/ldamodel.py:1077: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np

In [50]:
from pprint import pprint

# Print the Keyword in the 10 topics
pprint(lda_model_n.print_topics())
doc_lda = lda_model_n[bow_corpus_full]

INFO : topic #0 (0.021): 0.022*"autoridade" + 0.021*"criança" + 0.021*"internacional" + 0.019*"pescar" + 0.019*"brasileiro" + 0.017*"embarcação" + 0.016*"adolescente" + 0.015*"desportivo" + 0.015*"direito" + 0.013*"pesqueiro"
INFO : topic #22 (0.022): 0.091*"pontar" + 0.035*"instalação" + 0.030*"portuário" + 0.028*"área" + 0.028*"ambiental" + 0.020*"linha" + 0.018*"marítimo" + 0.016*"conservação" + 0.015*"água" + 0.014*"serviço"
INFO : topic #16 (0.025): 0.048*"produto" + 0.016*"órgão" + 0.014*"infração" + 0.012*"estabelecimento" + 0.010*"registrar" + 0.009*"competente" + 0.009*"técnico" + 0.008*"prazo" + 0.008*"abastecimento" + 0.008*"embalagem"
INFO : topic #4 (0.026): 0.022*"prazo" + 0.020*"armar" + 0.019*"lei" + 0.017*"autoridade" + 0.015*"autorização" + 0.010*"decisão" + 0.010*"redação" + 0.009*"procedimento" + 0.009*"documentar" + 0.008*"hipótese"
INFO : topic #12 (0.028): 0.038*"instituição" + 0.032*"ensinar" + 0.030*"rural" + 0.025*"curso" + 0.019*"familiar" + 0.017*"básico" + 

[(0,
  '0.022*"autoridade" + 0.021*"criança" + 0.021*"internacional" + '
  '0.019*"pescar" + 0.019*"brasileiro" + 0.017*"embarcação" + '
  '0.016*"adolescente" + 0.015*"desportivo" + 0.015*"direito" + '
  '0.013*"pesqueiro"'),
 (22,
  '0.091*"pontar" + 0.035*"instalação" + 0.030*"portuário" + 0.028*"área" + '
  '0.028*"ambiental" + 0.020*"linha" + 0.018*"marítimo" + 0.016*"conservação" '
  '+ 0.015*"água" + 0.014*"serviço"'),
 (16,
  '0.048*"produto" + 0.016*"órgão" + 0.014*"infração" + '
  '0.012*"estabelecimento" + 0.010*"registrar" + 0.009*"competente" + '
  '0.009*"técnico" + 0.008*"prazo" + 0.008*"abastecimento" + '
  '0.008*"embalagem"'),
 (4,
  '0.022*"prazo" + 0.020*"armar" + 0.019*"lei" + 0.017*"autoridade" + '
  '0.015*"autorização" + 0.010*"decisão" + 0.010*"redação" + '
  '0.009*"procedimento" + 0.009*"documentar" + 0.008*"hipótese"'),
 (12,
  '0.038*"instituição" + 0.032*"ensinar" + 0.030*"rural" + 0.025*"curso" + '
  '0.019*"familiar" + 0.017*"básico" + 0.017*"agrário" + 

In [51]:
pyLDAvis.enable_notebook()
LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model_n, bow_corpus_full, dictionary)
LDAvis_prepared

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
19    -0.090026 -0.142974       1        1  8.489058
9     -0.139840  0.029945       2        1  7.847724
15    -0.095208  0.188836       3        1  6.926000
3     -0.014977 -0.274410       4        1  6.711714
18     0.010771 -0.193006       5        1  5.600977
4     -0.103182  0.067031       6        1  4.771096
16    -0.119465  0.054850       7        1  4.760956
21    -0.121617 -0.010494       8        1  4.734369
20    -0.081015  0.018433       9        1  4.703680
23    -0.108246  0.138303      10        1  4.609470
13     0.156352 -0.006256      11        1  4.293113
5     -0.098001  0.159268      12        1  3.977039
1     -0.027629  0.033548      13        1  3.817889
6     -0.077053 -0.090736      14        1  3.381343
7      0.105426 -0.174009      15        1  3.060925
2     -0.103988  0.110109      16        1  3.002233
12    -0.082195 -0.072038      17        1  2.982807
11     0.225343  0.154137      18        1  2.914480
8      0.360158  0.038580      19        1  2.648278
24     0.378560  0.063416      20        1  2.117212
17     0.045211  0.011078      21        1  2.085249
14    -0.047087  0.058411      22        1  1.757379
22     0.014640 -0.079643      23        1  1.716163
0     -0.013434 -0.082135      24        1  1.608589
10     0.026499 -0.000245      25        1  1.482260, topic_info=            Term          Freq         Total Category  logprob  loglift
70     repúblico  12234.000000  12234.000000  Default  30.0000  30.0000
306      redação   8807.000000   8807.000000  Default  29.0000  29.0000
189      produto   5706.000000   5706.000000  Default  28.0000  28.0000
120          lei  15370.000000  15370.000000  Default  27.0000  27.0000
78        social   6262.000000   6262.000000  Default  26.0000  26.0000
..           ...           ...           ...      ...      ...      ...
110       fiscal    133.471622   2933.669975  Topic25  -4.8827   1.1215
357     controlo    128.056685   2759.904832  Topic25  -4.9241   1.1411
305  providência    123.668862   2601.392624  Topic25  -4.9589   1.1654
66       recurso    136.238632   6161.242260  Topic25  -4.8621   0.4000
18      conferir    126.150251   4909.878979  Topic25  -4.9391   0.5501

[1779 rows x 6 columns], token_table=      Topic      Freq  Term
term                       
5486     18  0.938711     1
6211     11  0.967929  1011
3147     11  0.953798  1013
1049     11  0.986037  1014
3934     11  0.897989  1022
...     ...       ...   ...
1435      8  0.078577  útil
1435      9  0.026716  útil
1435     10  0.006286  útil
1435     12  0.523320  útil
1435     13  0.029859  útil

[6330 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[20, 10, 16, 4, 19, 5, 17, 22, 21, 24, 14, 6, 2, 7, 8, 3, 13, 12, 9, 25, 18, 15, 23, 1, 11])